In [1]:
import numpy as np
import math
import pandas as pd
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt

# Data Acquisition
Dataset Description:
* 6 hand movements captured. 
* 3000 instances. 
* Two forearm surface EMG electrodes at Flexor Capri Ulnaris and Extensor Capri Radialis
* Sampling rate of 500 Hz.
* Filtered via a Butterworth Band Pass Filter with low and high cut-off at 15Hz and 500 Hz. Notch filter at 50 Hz.

<center><img src="Data/grasps_en.PNG" width="360" height="360"></center>

### Data Loading

5 subjects, 6 classes, 30 repetitions --> 900 data samples

### Note:
* To not include the effect of bias, the forward module has to be changed, in this case, even though the bias is being updated, it's effect is not seen in the model. Basically a dummy calculation

In [2]:
wavelets = ["bior3.5","bior1.5","bior3.9","coif3","coif5","db2","db9","haar","sym3","sym5","sym7"]
wave_type = 4
filename = "./Data/CSV/" + str(wavelets[wave_type]) + "_target.csv"
print(filename)
Y = pd.read_csv(filename, header=None)
Y = np.array(Y)
print(Y.shape)

filename = "./Data/CSV/" + str(wavelets[wave_type]) + "_ADDD.csv"
print(filename)
X = pd.read_csv(filename, header=None)
X = np.array(X)
print(X.shape)

N = X.shape[1]

X_train, X_test, Y_train, Y_test = train_test_split(X.T, Y.T, test_size = 0.3, random_state = 0,shuffle = True)


X_train = X_train.T
X_test = X_test.T
Y_train = Y_train.T
Y_test = Y_test.T

X_MAX = 1
X_MIN = -1
Xmin = np.min(X_train,axis=1)
Xmin = Xmin.reshape(Xmin.shape[0],1)
Xmax = np.max(X_train,axis=1)
Xmax = Xmax.reshape(Xmax.shape[0],1)

X_train = ((X_MAX - X_MIN) * (X_train - Xmin)/(Xmax-Xmin)) + Xmin
X_test = ((X_MAX - X_MIN) * (X_test - Xmin)/(Xmax-Xmin)) + Xmin

print(X_train.shape)
print(X_test.shape)
print(Y_train.shape)
print(Y_test.shape)

./Data/CSV/coif5_target.csv
(6, 900)
./Data/CSV/coif5_ADDD.csv
(8, 900)
(8, 630)
(8, 270)
(6, 630)
(6, 270)


### Activation Functions

$$linear(z) = z$$
$$relu(z) = max(0, z)$$
$$sigmoid(z) = 1 / (1 + e^{-z})$$
$$tanh(z) = 2/(1+e^{-2z})-1$$
$$softplus(z) = ln(1+e^{z})$$
$$Gaussian(z) = -z*e^{\frac{z^2}{2}}$$
$$MexicanHat(z) = (1-z^2)*e^{\frac{z^2}{2}}$$
$$MorletI(z) =0 cos(1.75z)*e^{\frac{z^2}{2}}$$
$$MorletII(z) = cos(5z)*e^{\frac{z^2}{2}}$$


In [3]:
def act_function(z,activation):
    """
    Inputs:
        z : z can either be a number or a numpy array
        activation: Python string denoting the activation function to be used in the current layer 
    Outputs:
        Activation function applied to z; if z is an array, the function must be applied to its each element
    """
    if activation == "linear":
        return z
    elif activation == "relu":
        return z*(z>0)
    elif activation == "sigmoid":
        return 1 / (1 + np.exp(-1*z))
    elif activation == "tanh":
        return (2 / (1 + np.exp(-2*z))) -1
    elif activation == "softplus":
        return np.log(1+ np.exp(z))
    elif activation == "softmax":
        e = z - np.max(z)
        return np.exp(e)/np.sum(np.exp(e))
    elif activation == "gaussian_wavelet":
        return -z*np.exp(-0.5*(z**2))
    elif activation == "mexican_hat_wavelet":
        return (1-(z**2))*np.exp(-0.5*(z**2))
    elif activation == "morlet_wavelet_1":
        return np.cos(1.75*z)*np.exp(-0.5*(z**2))
    elif activation == "morlet_wavelet_2":
        return np.cos(5*z)*np.exp(-0.5*(z**2))

### Initializing the Weights
The WNN will contain $H=1$ hidden layer and an output layer. For a layer $h$, we will have two parameters/variables:
  * Weight matrix $W^{[h]}$(of shape (size of current layer, size of previous layer)),
  * Bias vector $bias^{[h]}$(of shape (size of current layer, 1), 
  * Wavelet scaling factor $a^{[h]}$(of shape (size of current layer, 1),
  * Wavelet translation factor $b^{[h]}$(of shape (size of current layer, 1),

*   Used np.random.uniform(low, high, shape), with low=0.0 and high=0.01 to initialize the weights $W^{[h]}$ (<a href="https://docs.scipy.org/doc/numpy-1.15.0/reference/generated/numpy.random.uniform.html#numpy-random-uniform">np.random.uniform()</a>).a

*   Used np.random.uniform(low, high, shape), with low=0.0 and high=5 to initialize the scaling factor $a^{[h]}$ (<a href="https://docs.scipy.org/doc/numpy-1.15.0/reference/generated/numpy.random.uniform.html#numpy-random-uniform">np.random.uniform()</a>).

*   Used np.random.uniform(low, high, shape), with low=-10.0 and high=10 to initialize the translation factor $b^{[h]}$ (<a href="https://docs.scipy.org/doc/numpy-1.15.0/reference/generated/numpy.random.uniform.html#numpy-random-uniform">np.random.uniform()</a>).

*   Initialized biases $b^{[h]}$ with zeros (<a href="https://docs.scipy.org/doc/numpy/reference/generated/numpy.zeros.html">np.zeros()</a>).

* **For Normal Neural Network a is initialized to 1 and b to 0**


* For a single-hidden layer NN with input of size 5, hidden layer size = 4 and output layer size =3, the input parameter ```layers_sizes``` will be **[5, 4, 3]**. The output of the ```construct_WNN()``` function will be  **```[[np.array(shape=(4, 5)), np.array(shape=(4, 1))], np.array(shape=(4, 1))], np.array(shape=(4, 1))], [np.array(shape=(3, 4)), np.array(shape=(3, 1))]]```**, with each numpy array initialised as mentioned above.`

In [4]:
def construct_WNN(layers_sizes,weight_types):
    """
    Inputs:
        layers_sizes: A list (of length H+2) containing the size (number of neurons) of each layer. Element at index 0 represents input layer size.  
        weight_types = A list denoting if the activation layer is of Normal/Wavelet type
    Outputs:
        weights: A list (of length H), where each element is a list - [Wh, biash,ah,bh], representing the  weights matrix and bias vector of layer h (Both Wh and bh are numpy arrays).
    """
    low_W = 0
    high_W = 0.01
    low_a = 0
    high_a = 5
    low_b = -10
    high_b = 10
    H = len(layers_sizes)-2
    weights = []
    for h in range(H+1):
        w = np.random.uniform(low_W, high_W, (layers_sizes[h+1],layers_sizes[h]))
        bias = np.zeros((layers_sizes[h+1],1))
        if(weight_types[h] == 'Normal'):
            weights.append([w,bias])
        elif(weight_types[h] == 'Wavelet'):
            a = np.random.uniform(low_a, high_a, (layers_sizes[h+1],1))
            b = np.random.uniform(low_b, high_b, (layers_sizes[h+1],1))
            weights.append([w,bias,a,b])
    return weights 

### Forward Propagation
This function carries out computations of a single layer of the neural network:
 $$ Z^{[h]} = W^{[h]}.A^{[h-1]}+bias^{[h]}$$
 $$ A^{[h]} = g^{[h]}(Z^{[h]}) $$

In [31]:
def forward_step(A_prev, weight, activation,take_bias,weight_type):
    """
    Inputs:
        A_prev: Input data OR Previous layer's activations of shape (size of previous layer, number of examples)
        W: List of trainables
        activation: Python string denoting the activation function to be used in the current layer 
        take_bias: True -> Take bias, False -> No Bias
        weight_type = A string denoting if the activation layer is of Normal/Wavelet type
    Outputs:
        A: Current layer's activations of shape (size of current layer, number of examples)
        Z: Current layer's pre activation value, i.e. input of activation function
    """
    if(weight_type == 'Normal'):
        W = weight[0]
        bias = weight[1]
        a=None
        b=None
        if(take_bias):
            Z = W.dot(A_prev)+bias
        else:
            Z = W.dot(A_prev)
    elif(weight_type == 'Wavelet'):
        W = weight[0]
        bias = weight[1]
        a = weight[2]
        b = weight[3]
        if(take_bias):
            Z = W.dot(A_prev)+bias
        else:
            Z = W.dot(A_prev)
        Z = (Z-b)/a
        
    A = act_function(Z, activation)
    try:
        assert(np.any(np.isnan(A)))
        assert(np.any(np.isnan(Z)))
    except: 
        print(W)
        print(bias)
        print(a)
        print(b)
    return A, Z

###  Forward Propagation Module
* This function iterates over the $H$ layers of the neural network using a for loop, computing the final output of the neural network. 
* It also outputs a ```layers_cache``` list (of length H), whose each element corresponds to a layer $h$ and is a list[$A^{[h-1]}, W^{[h]}, Z^{[h]}$]. Storing these values now will be helpful while computing gradients n the backward pass.
* For the sake of clarity, consider a single-hidden layer NN with input of size 5, hidden layer size = 4 and output layer size =3. For this example, the output ```layers_cache``` list will be [[$X or A^{[0]}$, $W^{[1]}$, $Z^{[1]}$], [$A^{[1]}$, $W^{[2]}$, $Z^{[2]}$]].

In [32]:
def forward_module(X, weights, activations,take_bias,weight_types):
    """
    Inputs:
        X: Input data of shape (size of input layer, number of examples)
        weights: A list (of length H), where each element is a list -[Wh, biash] OR [Wh, biash,ah,bh], representing the weights matrix and bias vector of layer h (Both Wh and bh are numpy arrays).
        activations: A list (of length H), where each element is a Python string representing the activation function to be used in the corresponding layer
        take_bias: Take bias, False -> No Bias
        weight_types = A list denoting if the activation layer is of Normal/Wavelet type
    Outputs:
        AH: Output layer's activations
        layers_cache: A list (of length H), where each element is a list [A_prev, W, a, b, Z], representing the values A_prev (input to the layer), W (Weight matrix of the layer),a (scaling factor of the layer), b (translation factor of the layer)
          and Z (pre-activation value) for layer h. The purpose of cache is to store values that will be needed during backpropagation.
    """
    layers_cache = []
    H = len(weights)
    A = X

    for h in range(H):
        activation = activations[h]
        #     print('{}, weight {}'.format(h, weights[h][0].shape))
        _,Z = forward_step(A, weights[h],activation,take_bias,weight_types[h])
        if(weight_types[h] == 'Wavelet'):
            layers_cache.append([A,weights[h][0],weights[h][2],weights[h][3],Z]) #A_prev, weight, a, b, pre-activation output
        elif(weight_types[h] == 'Normal'):
            layers_cache.append([A,weights[h][0],None,None,Z]) 
        A,_ = forward_step(A, weights[h],activation,take_bias,weight_types[h])

    return A, layers_cache

###  Cost Function
Compute the mean square error cost using the following formula: $$\frac{1}{m}\left(\frac{1}{2} \sum\limits_{i = 1}^{m} \left(y^{(i)} - \left(a^{[H] (i)}\right)\right)^2\right) $$

Compute the cross entropy error cost using the following formula: $$-\frac{1}{m} \sum\limits_{i = 1}^{m} \left(y^{(i)}*\log\left(a^{[H] (i)}\right)\right)$$

where  
$$m = number \ of \ examples$$
$$ y^{(i)} = Ground \ truth \ labels \ for \ i-th \ example $$
$$ a^{[H](i)} = Output \ layer \ activations \ for \ i-th \ example $$
$$ * \ denotes \ elementwise \ multiplication $$


In [33]:
def cost_function(AH, Y,error_function):
    """
    Inputs:
        AH: Activations of output layer, representing probability vector corresponding to your label predictions, of shape (1, number of examples)
        Y: Ground truth "label" vector of shape (1, number of examples)
        error_function: mean_square / cross_entropy
    Outputs:
        cost: Cost of shape () i.e. scalar value
    """
    m = Y.shape[1]
    if(error_function == "mean_square"):
        cost = (1/(2*m))*np.sum(np.square(Y-AH))
    elif(error_function == "cross_entropy"):
        cost = (-1/m)*((np.multiply(Y,np.log(AH))).sum())
    
    return cost

###  Activation Backward Propagation
This function computes  $dZ^{[h]} = \frac{\partial \mathcal{L} }{\partial Z^{[h]}}$, given  $dA^{[h]} = \frac{\partial \mathcal{L} }{\partial A^{[h]}}$ and $Z^{[h]}$as inputs. It is based on the following chain rule from calculus:
$$ dZ^{[h]} = dA^{[h]} * \frac{\partial \mathcal{A^{[h]}} }{\partial Z^{[h]}}$$

<br> For Wavelet: <br>
$$ dZ'^{[h]} = dA^{[h]} * \frac{\partial \mathcal{A^{[h]}} }{\partial Z'^{[h]}}$$

Note the following rules for different activation functions:
$$ \frac{\partial \mathcal{(relu(z))} }{\partial z} =   \left\{
\begin{array}{ll}
      1 & z>=0 \\
      0& z < 0 \\
\end{array} 
\right.  $$<br>
$$\frac{\partial \mathcal{(sigmoid(z))} }{\partial z} = sigmoid(z) * (1-sigmoid(z))$$<br>
$$\frac{\partial \mathcal{(tanh(z))} }{\partial z} = 1-tanh(z)*tanh(z)$$<br>
$$\frac{\partial \mathcal{(softplus(z))} }{\partial z} = sigmoid(z) $$<br>
$$\frac{\partial \mathcal{(Gaussian Wavelet(z))} }{\partial z} = -Mexican Hat(z) $$<br>
$$\frac{\partial \mathcal{(Mexican Hat Wavelet(z))} }{\partial z} = Gaussian(z) * (1-z^2) $$<br>
$$\frac{\partial \mathcal{(Morelet Wavelet I(z))} }{\partial z} = -e^{-\frac{t^2}{2}}*\left(1.75*sin(1.75t) + t*cos(1.75t)\right) $$<br>
$$\frac{\partial \mathcal{(Morlet Wavelet II(z))} }{\partial z} = e^{-\frac{t^2}{2}}*\left(5*sin(5t) + t*cos(5t)\right) $$<br>

In [34]:
def act_backward(dA, Z,activation):
    """
    Inputs:
        dA: Gradient of the cost function w.r.t. the post activation value A, of shape(size of current layer, number of examples)
        Z: Pre activation value, of shape(size of current layer, number of examples)
        activation: Python string denoting the activation function to be used in the current layer 
    Outputs:
        dZ: Gradient of the cost function w.r.t. Z, of shape(size of current layer, number of examples)
    """
    if activation == "linear":
        dZ = dA
    elif activation == "relu":
        dZ = dA*(Z>=0)
    elif activation == "sigmoid":
        dZ = dA*act_function(Z,'sigmoid')*(1- act_function(Z,'sigmoid'))
    elif activation == "tanh":
        dZ = np.multiply(dA,(1- act_function(Z,'tanh')*act_function(Z,'tanh')))
    elif activation == "softplus":
        dZ = dA*act_function(Z,'sigmoid')
    elif activation == "softmax":
        dZ = dA #dA*(act_function(Z,'softmax')-1)
    elif activation == 'gaussian_wavelet':
        dZ = dA*(-1*act_function(Z,'mexican_hat_wavelet'))
    elif activation == 'mexican_hat_wavelet':
        dZ = dA*(np.multiply(act_function(Z,'gaussian_wavelet'), (3-Z**2)))
    elif activation == 'morlet_wavelet_1':
        dZ = dA*(np.multiply(np.exp(-0.5*(z**2)), (1.75*np.sin(1.75*Z)+ Z*np.cos(1.75*Z))))
    elif activation == 'morlet_wavelet_2':
        dZ = dA*(np.multiply(np.exp(-0.5*(z**2)), (5*np.sin(5*Z)+ Z*np.cos(5*Z))))
    return dZ


### Backward Propagation Step
* The following function computes $dA^{[h-1]}, dW^{[h]}$ and $db^{[h]}$, given $dA^{[h]}, Z^{[h]}, W^{[h]}$ and $A^{[h-1]}$ as inputs.  
* We can calculate $dZ^{[h]}$ using $dA^{[h]}$ and $Z^{[h]}$ as inputs to the ```activation_backward()``` function defined above.  
* The three outputs $(dA^{[h-1]}, dW^{[h]}, dbias^{[h]})$ are computed using $dZ^{[h]}, W^{[h]}$ and $A^{[h-1]}$ using the below equations(using the fact that $ Z^{[h]} = W^{[h]}.A^{[h-1]}+b^{[h]}$): 
 <br> If Normal:<br>
  - $ dA^{[h-1]} = \frac{\partial \mathcal{L} }{\partial A^{[h-1]}} = W^{[h] T} dZ^{[h]}$
  - $ dW^{[h]} = \frac{\partial \mathcal{L} }{\partial W^{[h]}} = \frac{1}{m} dZ^{[h]} A^{[h-1] T}$
  - $ dbias^{[h]} = \frac{\partial \mathcal{L} }{\partial bias^{[h]}} = \frac{1}{m} \sum_{i = 1}^{m} dZ^{[h](i)}$
  <br>If Wavelet:<br>
  - $ dA^{[h-1]} = \frac{\partial \mathcal{L} }{\partial A^{[h-1]}} = W^{[h] T} dZ'^{[h]}*\frac{1}{a^{[h](i)}}$
  - $ dW^{[h]} = \frac{\partial \mathcal{L} }{\partial W^{[h]}} = \frac{1}{m} dZ'^{[h]} A^{[h-1] T}*\frac{1}{a^{[h](i)}}$
  - $ dbias^{[h]} = \frac{\partial \mathcal{L} }{\partial bias^{[h]}} = \frac{1}{m} \sum_{i = 1}^{m} dZ'^{[h](i)}*\frac{1}{a^{[h](i)}}$
  - $ da^{[h]} = \frac{\partial \mathcal{L} }{\partial a^{[h]}} = \frac{1}{m} \sum_{i = 1}^{m} dZ'^{[h](i)}*(-1)*\frac{Z'^{[H](i)}}{a^{[h](i)}}$
  - $ db^{[h]} = \frac{\partial \mathcal{L} }{\partial b^{[h]}} = \frac{1}{m} \sum_{i = 1}^{m} dZ'^{[h](i)}*(-1)\frac{1}{a^{[h](i)}}$


In [35]:
def backward_step(dA, layer_cache, activation,weight_type):
    """
    Inputs:
        dA: Gradient of the cost function w.r.t. the post activation value A for current layer
        layer_cache: A list [A_prev, W, a, b,Z] for current layer, where A_prev is activation of prev layer, W is weight matrix of current layer, and Z is pre-activation value for current layer
        activation: Python string denoting the activation function used in the current layer
        weight_type = A string denoting if the activation layer is of Normal/Wavelet type
    Outputs:
        dA_prev: Gradient of the cost function w.r.t. the activation (of the previous layer h-1), of same shape as A_prev
        dW: Gradient of the cost function w.r.t. W (current layer l), of same shape as W
        dbias: Gradient of the cost function w.r.t. bias (current layer l), of same shape as bias
        da: Gradient of the cost function w.r.t. a (current layer l), of same shape as a
        db: Gradient of the cost function w.r.t. b (current layer l), of same shape as b
    """
    if(weight_type == 'Wavelet'):
        A_prev = layer_cache[0]
        W = layer_cache[1]
        a = layer_cache[2]
        b = layer_cache[3]
        Z = layer_cache[4] #Actually Z'
    elif(weight_type == 'Normal'):
        A_prev = layer_cache[0]
        W = layer_cache[1]
        Z = layer_cache[4]
    
    m = Z.shape[1]
    dZ = act_backward(dA,Z,activation)
    if(weight_type == 'Wavelet'):
        dZ = dZ / a # dZ = dZ' /a
    
    dA_prev = np.matmul((W.T),dZ)
    dW = (np.matmul(dZ,A_prev.T))/m
    dbias = (np.sum(dZ,axis =1,keepdims = True))/m
    if(weight_type == 'Wavelet'):
        da = np.sum((dZ * (-1) * Z),axis = 1, keepdims = True)/m # Z-b/a == Z' which is Z in the code (retrieved from cache layer)
        db = np.sum((dZ * (-1)),axis = 1, keepdims = True)/m
        return dA_prev, dW, dbias,da,db
    elif(weight_type == 'Normal'):
        return dA_prev, dW, dbias,None, None

### Backward Propagation Module 
* This function computes the gradients of loss function w.r.t. all the weights of the neural network.
* To backpropagate through this network, we know that the output is, $A^{[H]} = linear(Z^{[H]})$. Thus compute $ dA^{[h]} = \frac{\partial \mathcal{L}}{\partial A^{[H]}}$. To do so, use this formula:
$$ dA^{[h]} = -\left(Y - A^{[h]}\right)$$
where $ "/" \ denotes \ elementwise \ division$
* The output of this function is a list ```gradients``` of length $H$, whose each element is a list [$dW^{[h]}, db^{[h]}$].
* For the sake of clarity, consider a single-hidden layer NN with input of size 5, hidden layer size = 4 and output layer size =3. For this example, the output ```gradients``` will be [[$dW^{[1]}, db^{[1]}$], [$dW^{[2]}, db^{[2]}$]].

In [36]:
### 1.5 Marks
def backward_module(AH, Y, layers_cache, activations,error_function,weight_types):
    """
    Inputs:
        AH: Activations of output layer, representing probability vector corresponding to your label predictions, of shape (1, number of examples)
        Y: Ground truth "label" vector of shape (1, number of examples)
        layers_cache: A list (of length H), where each element is a list [A_prev, W, Z], representing the values A_prev (input to the layer), W (Weight matrix of the layer)
          and Z (pre-activation value) for layer h. The purpose of cache is to store values that will be needed during backpropagation.
        activations: A list (of length H), where each element is a Python string representing the activation function to be used in the corresponding layer
        error_function: mean_square / cross_entropy
        weight_types: A list denoting if the activation layer is of Normal/Wavelet type
    Outputs:
        gradients: A list (of length H), where each element is a list [dW, db], representing the values dW (gradient of cost function w.r.t. W) and  
          db (gradient of cost function w.r.t. b)
    """
    gradients = []
    H = len(layers_cache) # the number of layers
    m = AH.shape[1]
    Y = Y.reshape(AH.shape) 
    if(activations[-1] == "softmax", error_function == "mean_square"):
        try:
            dAH = np.multiply((Y-AH),AH).sum()*AH - np.multiply(Y-AH,AH)
        except:
            print(AH.shape)
            print(np.dot(((Y-AH).T),AH).shape)
            print(np.multiply(Y-AH,AH).shape)
            print(np.dot(((Y-AH).T),AH) - np.multiply(Y-AH,AH).shape)
        assert(dAH.shape == AH.shape)
    else:
        dAH = -(Y-AH) # Valid for MSE or Cross Entropy with Soft Max
    dA = dAH
    for i in reversed(range(H)):
        dA_prev, dW, dbias,da,db = backward_step(dA,layers_cache[i],activations[i],weight_types[i])
        gradients.insert(0,(dW,dbias,da,db))
        dA = dA_prev
    return gradients

### Batch Gradient Descent Optimizer
Now that we have calculated the gradients of the loss function w.r.t. all the weights of the network, update the weights of the model, using gradient descent: 

$$ W^{[h]} = W^{[h]} - \alpha \text{ } dW^{[h]} $$
$$ bias^{[h]} = bias^{[h]} - \alpha \text{ } dbias^{[h]} $$
$$ a^{[h]} = a^{[h]} - \alpha \text{ } da^{[h]} $$
$$ b^{[h]} = b^{[h]} - \alpha \text{ } db^{[h]} $$

where $\alpha$ is the learning rate.   
After computing the updated weights, store them back in the weights list. 

In [37]:
def update_weights(weights, gradients, lr,weight_types):
    """
    Inputs:
        weights: A list (of length H), where each element is a list - [Wh, bh], representing the weights matrix and bias vector of layer h (Both Wh and bh are numpy arrays).
        gradients: A list (of length H), where each element is a list - [dWh, dbh], representing the gradients of cost function w.r.t. weights matrix and bias vector 
          of layer h respectively (Both dWh and dbh are numpy arrays).
        lr: Learning Rate
        weight_types: A list denoting if the activation layer is of Normal/Wavelet type
    Outputs:
        weights: A list (of length H), containing the updated weights.
    """
    H = len(weights)
    for h in range(H):
        weights[h][0] -= lr*gradients[h][0]
        weights[h][1] -= lr*gradients[h][1]
        if(weight_types[h] == 'Wavelet'):
            weights[h][2] -= lr*gradients[h][2]
            weights[h][3] -= lr*gradients[h][3]    
    return weights

### Train a H-layer Neural Network:
This function performs the following steps:  
1. Initialize the weights of the neural network .
2. Perform forward propagation on input argument ```X```.
3. Compute cross entropy loss function.
4. Perform backward propagation to compute gradients of loss function w.r.t. all the weights of the network.
5. Use the gradients computed in step 4 to update the weights of the network.
6. Append cost's value to the list ```epoch_wise_costs```.
7. Print (epoch, cross entropy cost's value) for epoch = 0, 100, 200, ...
8. Repeat steps 2-7 for ```epochs```(input argument to below function) number of iterations.
9. Return the weights of the neural network.


In [38]:
def H_layer_NN(X, Y, layers_sizes, activations, epochs, lr, take_bias,error_function,weight_types):
    """
    Inputs:
        X: Input data, numpy array of shape (number_of_features_in_input_data, number of examples)
        Y: Ground truth "label" vector of shape (1, number of examples)
        layers_sizes: A list (of length H+1) containing the size (number of neurons) of each layer. Element at index 0 represents input layer size.
        activations: A list (of length H), where each element is a Python string representing the activation function to be used in the corresponding layer
        epochs: number of epochs of the training loop
        lr: learning rate of the gradient descent update rule
        take_bias: Take bias, False -> No Bias
        error_function: mean_square / cross_entropy
        weight_types: A list denoting if the activation layer is of Normal/Wavelet type
    Outputs:
        weights - weights learnt by the model (can be used for prediction). A list (of length H), where each element is a list - [Wh, bh], representing the weights matrix and bias vector of layer h.
    """
    epoch_wise_costs = []
    AH = None
    weights = construct_WNN(layers_sizes,weight_types)
    for epoch in range(epochs):
        AH, layers_cache = forward_module(X, weights, activations,take_bias,weight_types)
        cost = cost_function(AH, Y,error_function)
        gradients = backward_module(AH, Y, layers_cache, activations,error_function,weight_types)
        
        update_weights(weights, gradients, lr,weight_types)
        epoch_wise_costs.append(cost)
        if epoch % 100 == 0 or epoch == epochs -1:
            print("Cost after epoch %i: %f" %(epoch, cost))
    if(weight_types[0] == "Normal"):
        plt.plot(np.array(epoch_wise_costs), "r")
    elif(weight_types[0] == "Wavelet"):
        plt.plot(np.array(epoch_wise_costs),"g")
    plt.ylabel('Cost Function')
    plt.xlabel('Number of Epochs')
    plt.title("Training Curve")

    return weights

In [39]:
def predict(X, Y, weights, activations, mode,take_bias, error_function,weight_types):
    """
    Inputs:
        X: Input data/examples you would like to predict
        Y: Ground truth labels corresponding to input data X
        weights: weights of the trained model
        activations: A list (of length H), where each element is a Python string representing the activation function to be used in the corresponding layer
        mode: Test/Training mode
        take_bias: Take bias, False -> No Bias
         error_function: mean_square / cross_entropy
        weight_types: A list denoting if the activation layer is of Normal/Wavelet type
    Outputs:
        p: predictions for the given dataset X
    """
    m = X.shape[1]
    AH, _ = forward_module(X, weights, activations, take_bias,weight_types)
    cost = cost_function(AH, Y,error_function)
    p = np.zeros_like(AH)
    p[AH == np.amax(AH,axis=0)] = 1
    for i in range(p.shape[1]):
        while(np.sum(p[:,i]) > 1):
            pos_pred = np.argmax(p[:,i])
            p[pos_pred,i] = 0
    correct = np.sum(np.argmax(p,axis=0) == np.argmax(Y,axis=0))
    NN_type = weight_types[0]
    print(str(NN_type) +" Neural Network: " + mode + " Cost: "  + str(cost))
    print(str(NN_type) +" Neural Network: " + mode + " Accuracy: "  + str(correct/m))
    return p

### Main Function

In [ ]:
layers_sizes = [8, 17, 6]
epochs = 10000
lr = 0.03
TAKE_BIAS = False
error_function = "mean_square"
activations_normal = ["tanh","linear"]
activations_wavelet = ["gaussian_wavelet","linear"]
weight_types_NN = ["Normal","Normal"]
weight_types_WNN = ["Wavelet","Normal"]
print("******************** NORMAL ARTIFICIAL NEURAL NETWORK ********************")
weights_normal = H_layer_NN(X_train, Y_train, layers_sizes, activations_normal, epochs, lr, TAKE_BIAS,error_function,weight_types_NN)
print("******************** NORMAL ARTIFICIAL NEURAL NETWORK PREDICTION********************")
training_predictions_normal = predict(X_train, Y_train, weights_normal, activations_normal, "Train",TAKE_BIAS,error_function,weight_types_NN)
# test_predictions_normal = predict(X_test, Y_test, weights_normal, activations_normal, "Test",False,weight_types_NN)
print("******************** WAVELET NEURAL NETWORK ********************")

weights_wavelet = H_layer_NN(X_train, Y_train, layers_sizes, activations_wavelet, epochs, lr, TAKE_BIAS,error_function,weight_types_WNN)
print("******************** WAVELET NEURAL PREDICTION ********************")
training_predictions_wavelet = predict(X_train, Y_train, weights_wavelet, activations_wavelet, "Train",TAKE_BIAS,error_function,weight_types_WNN)
# test_predictions_wavelet = predict(X_test, Y_test, weights_wavelet, activations_wavelet, "Test",TAKE_BIAS,weight_types_WNN)
plt.legend(["Normal","Wavelet"])

******************** NORMAL ARTIFICIAL NEURAL NETWORK ********************
[[0.00223635 0.00198842 0.00963036 0.00851622 0.00939628 0.00043699
  0.00408575 0.00171295]
 [0.00101579 0.00730681 0.00842041 0.00490388 0.00874688 0.00639488
  0.00372373 0.00299433]
 [0.00629476 0.00795076 0.00181447 0.0074988  0.00362849 0.00838915
  0.00549211 0.00855643]
 [0.00157064 0.00275167 0.00019586 0.00645756 0.00065448 0.0036448
  0.0005688  0.00555092]
 [0.00679053 0.00055611 0.00314726 0.00523633 0.00803382 0.00491987
  0.00200394 0.0078653 ]
 [0.00274291 0.00189448 0.00799484 0.00091598 0.00530428 0.00703843
  0.00858506 0.00460156]
 [0.00952638 0.00554315 0.00289936 0.00713719 0.00364772 0.00736863
  0.00979272 0.00208471]
 [0.00369186 0.00672442 0.00542644 0.00815762 0.00325635 0.00419278
  0.00647873 0.00957285]
 [0.00194527 0.00893974 0.0059575  0.00499584 0.00867071 0.0095486
  0.00646366 0.00449516]
 [0.00873762 0.00535432 0.00395236 0.00430865 0.00057902 0.00632488
  0.00169346 0.0091953

  6.63359564e-03]]
[[-0.00059222]
 [-0.00058744]
 [-0.00056401]
 [-0.00056062]
 [-0.00048845]
 [-0.00087111]]
None
None
[[0.0022186  0.00197489 0.0096184  0.00850461 0.0093814  0.00042337
  0.00407135 0.0017061 ]
 [0.001003   0.00729706 0.00841178 0.00489552 0.00873616 0.00638509
  0.00371338 0.00298939]
 [0.00627566 0.00793626 0.00180168 0.00748638 0.00361244 0.00837446
  0.00547661 0.00854908]
 [0.00154943 0.00273554 0.00018163 0.00644375 0.00063669 0.00362851
  0.00055159 0.00554276]
 [0.00676951 0.00054006 0.00313303 0.00522251 0.00801627 0.00490392
  0.00198707 0.00785721]
 [0.00272604 0.00188158 0.00798341 0.00090488 0.00529021 0.00702559
  0.00857146 0.00459507]
 [0.00949877 0.00552211 0.00288071 0.0071191  0.00362462 0.00734759
  0.00977048 0.00207406]
 [0.00367167 0.00670891 0.00541272 0.00814426 0.00323952 0.00417733
  0.00646233 0.00956506]
 [0.00192232 0.0089223  0.00594213 0.00498091 0.00865139 0.00953089
  0.00644496 0.0044863 ]
 [0.00871299 0.00533551 0.0039357  0.004292

  0.00556856 0.00477372]]
[[-3.94237126e-05]
 [-2.84349925e-05]
 [-4.26791758e-05]
 [-4.73274278e-05]
 [-4.68021206e-05]
 [-3.72772471e-05]
 [-6.15711213e-05]
 [-4.42692399e-05]
 [-5.12768709e-05]
 [-5.46765417e-05]
 [-5.10380344e-05]
 [-5.57691838e-05]
 [-5.22160925e-05]
 [-4.84248459e-05]
 [-3.09072982e-05]
 [-4.81417809e-05]
 [-3.70937060e-05]]
None
None
[[0.00219944 0.00196028 0.00960548 0.00849208 0.00936535 0.00040869
  0.00405582 0.00169871]
 [0.00098923 0.00728658 0.0084025  0.00488652 0.00872462 0.00637455
  0.00370223 0.00298408]
 [0.00625508 0.00792063 0.00178789 0.00747301 0.00359513 0.00835863
  0.00545991 0.00854116]
 [0.0015265  0.00271811 0.00016626 0.00642882 0.00061744 0.00361091
  0.000533   0.00553394]
 [0.00674682 0.00052274 0.00311767 0.0052076  0.00799733 0.0048867
  0.00196885 0.00784848]
 [0.00270785 0.00186766 0.00797107 0.0008929  0.00527504 0.00701173
  0.0085568  0.00458806]
 [0.00946896 0.00549939 0.00286058 0.00709959 0.00359968 0.00732489
  0.00974648 0.

   6.56792148e-03]]
[[-0.00188005]
 [-0.00186515]
 [-0.00179049]
 [-0.00178043]
 [-0.00155136]
 [-0.00276639]]
None
None
[[0.00218406 0.00194855 0.00959511 0.00848201 0.00935246 0.00039689
  0.00404334 0.00169278]
 [0.0009782  0.00727817 0.00839507 0.0048793  0.00871538 0.00636611
  0.0036933  0.00297982]
 [0.00623857 0.00790808 0.00177683 0.00746227 0.00358125 0.00834592
  0.00544651 0.00853481]
 [0.00150804 0.00270407 0.00015388 0.0064168  0.00060196 0.00359673
  0.00051803 0.00552684]
 [0.00672858 0.00050882 0.00310532 0.00519561 0.00798211 0.00487287
  0.00195422 0.00784146]
 [0.00269325 0.00185649 0.00796117 0.00088328 0.00526286 0.00700061
  0.00854502 0.00458243]
 [0.00944501 0.00548114 0.0028444  0.0070839  0.00357963 0.00730665
  0.00972718 0.00205334]
 [0.00363239 0.00667872 0.00538602 0.00811826 0.00320679 0.0041473
  0.00643045 0.0095499 ]
 [0.00187768 0.00888837 0.00591223 0.00495188 0.00861382 0.00949643
  0.00640859 0.00446908]
 [0.00866499 0.00529885 0.00390324 0.004260

None
[[ 2.01309346e-03  3.61762007e-03  2.53624897e-03  8.18032976e-03
   8.55339336e-03  3.11659805e-03  8.66063032e-03  8.61934738e-03
   3.02232128e-03  7.62771508e-03  5.87881190e-03  8.30834691e-03
   3.74717364e-04  4.35909349e-03  6.38867016e-03  7.27813346e-03
   2.50066289e-03]
 [ 3.30088170e-03  2.27474393e-03  8.36057177e-03  9.20928066e-03
   1.98503109e-03  2.80724238e-04  3.62947510e-03  3.90017799e-04
   9.90012412e-03  2.76676799e-03  8.89472695e-03  8.63295412e-03
   8.77071394e-03 -4.32120810e-05  5.87481495e-03  8.23935805e-03
   8.76764521e-03]
 [ 4.19332451e-03  9.36318854e-04  7.45855232e-03  9.53358574e-03
   4.21375076e-03  5.91931384e-03  4.03662437e-03  7.00895622e-04
   1.44511526e-03  5.56196997e-03  8.52401424e-03  8.11404403e-03
   9.64604865e-03  7.72654033e-03  3.34429171e-04  9.91832328e-04
   3.67130534e-03]
 [ 6.45328033e-03  7.23470424e-03  1.16463121e-03  4.27826930e-03
   3.97970336e-04  2.41867394e-03  8.17361138e-03  9.13368397e-03
   7.95765887e

...

[[ 0.00134759  0.00131032  0.00903082  0.00793436  0.00865169 -0.00024489
   0.00336459  0.00136994]
 [ 0.00042075  0.00685348  0.008019    0.00451477  0.00824815  0.00593972
   0.00324215  0.00276442]
 [ 0.00536522  0.00724552  0.00119318  0.00689572  0.00284589  0.00767247
   0.00473686  0.00819883]
 [ 0.00044137  0.00189306 -0.00056074  0.00572258 -0.0002935   0.00277666
  -0.00034797  0.00511677]
 [ 0.00572087 -0.00026144  0.0024211   0.00453134  0.00714208  0.00411075
   0.00114795  0.00745387]
 [ 0.00190646  0.00125337  0.00742597  0.00036345  0.004608    0.00640296
   0.00791179  0.00427941]
 [ 0.00812389  0.00447385  0.00195061  0.00621738  0.00247489  0.00630238
   0.00866514  0.00154402]
 [ 0.00268069  0.00594449  0.00473654  0.00748493  0.00241579  0.00341984
   0.00565696  0.0091825 ]
 [ 0.00080379  0.00807256  0.00519428  0.0042545   0.00770798  0.00866447
   0.00553104  0.00405449]
 [ 0.00746572  0.00438191  0.00309062  0.00347198 -0.00048283  0.00535598
   0.00066754  0.

   0.00495044  0.00448219]]
[[-0.0009535 ]
 [-0.00064034]
 [-0.00100732]
 [-0.00121794]
 [-0.00115167]
 [-0.00089178]
 [-0.00151267]
 [-0.00106524]
 [-0.00123525]
 [-0.00136268]
 [-0.00127376]
 [-0.00143562]
 [-0.00127797]
 [-0.00119467]
 [-0.00074793]
 [-0.00117276]
 [-0.00085559]]
None
None
[[ 0.00134274  0.00130662  0.00902755  0.00793118  0.00864764 -0.00024861
   0.00336066  0.00136807]
 [ 0.00041782  0.00685125  0.00801702  0.00451286  0.00824569  0.00593748
   0.00323978  0.00276329]
 [ 0.00536034  0.00724183  0.00118993  0.00689256  0.00284178  0.0076687
   0.00473289  0.00819695]
 [ 0.00043475  0.00188803 -0.00056516  0.00571827 -0.00029906  0.00277157
  -0.00035335  0.00511423]
 [ 0.00571492 -0.00026599  0.00241705  0.00452741  0.00713713  0.00410627
   0.00114321  0.00745158]
 [ 0.00190195  0.00124991  0.00742289  0.00036046  0.00460426  0.00639955
   0.00790818  0.00427768]
 [ 0.0081161   0.00446791  0.00194534  0.00621227  0.00246839  0.00629648
   0.0086589   0.00154101]


 [-0.0008599 ]]
None
None
[[ 1.18064455e-03  2.64283481e-03  1.46708590e-03  7.81961643e-03
   7.74426245e-03  2.26747234e-03  7.56230201e-03  7.64898172e-03
   1.91169114e-03  6.81085249e-03  5.15567120e-03  7.86951776e-03
  -5.79979693e-04  3.53440865e-03  5.75982378e-03  6.34016274e-03
   1.40689747e-03]
 [ 2.54231188e-03  1.37309627e-03  7.36761411e-03  8.88114023e-03
   1.22706218e-03 -5.20118694e-04  2.60487209e-03 -4.99491510e-04
   8.86200204e-03  2.01507494e-03  8.23205798e-03  8.22953797e-03
   7.88100360e-03 -8.00675253e-04  5.29156743e-03  7.37583226e-03
   7.75449612e-03]
 [ 3.37447093e-03 -2.84503370e-05  6.39742873e-03  9.17733554e-03
   3.41425092e-03  5.07319839e-03  2.94464197e-03 -2.59527694e-04
   3.41722377e-04  4.75421768e-03  7.80978774e-03  7.68041460e-03
   8.69901024e-03  6.91656305e-03 -2.89174541e-04  6.72350032e-05
   2.58922976e-03]
 [ 5.63779119e-03  6.27186782e-03  1.05392548e-04  3.92379950e-03
  -4.01365781e-04  1.57110543e-03  7.08372173e-03  8.176004

[[ 0.00133256  0.00129885  0.00902068  0.00792451  0.0086391  -0.00025643
   0.00335239  0.00136413]
 [ 0.00041169  0.00684658  0.00801288  0.00450885  0.00824054  0.00593279
   0.00323482  0.00276091]
 [ 0.0053501   0.00723407  0.00118311  0.00688594  0.00283313  0.00766078
   0.00472456  0.00819302]
 [ 0.00042081  0.00187744 -0.00057449  0.00570921 -0.00031077  0.00276083
  -0.00036468  0.00510888]
 [ 0.0057024  -0.00027557  0.00240853  0.00451913  0.00712672  0.00409685
   0.00113324  0.00744677]
 [ 0.00189248  0.00124264  0.00741642  0.00035418  0.0045964   0.00639238
   0.00790058  0.00427403]
 [ 0.00809974  0.00445543  0.00193424  0.00620152  0.00245472  0.00628407
   0.00864578  0.0015347 ]
 [ 0.00266357  0.00593121  0.00472479  0.00747345  0.0024016   0.00340676
   0.00564302  0.00917589]
 [ 0.00078466  0.00805804  0.00518152  0.0042421   0.0076918   0.00864957
   0.00551535  0.0040471 ]
 [ 0.00744336  0.00436479  0.00307544  0.00345724 -0.00050147  0.00533899
   0.00064954  0.

   0.00494038  0.00447746]]
[[-0.00096941]
 [-0.00064998]
 [-0.00102357]
 [-0.00123986]
 [-0.00117132]
 [-0.00090644]
 [-0.00153842]
 [-0.00108289]
 [-0.00125575]
 [-0.00138631]
 [-0.00129586]
 [-0.00146148]
 [-0.00129961]
 [-0.00121512]
 [-0.00076041]
 [-0.0011925 ]
 [-0.00086894]]
None
None
[[ 1.17022294e-03  2.63022708e-03  1.45352335e-03  7.81580185e-03
   7.73434828e-03  2.25681319e-03  7.54879764e-03  7.63682497e-03
   1.89778038e-03  6.80101440e-03  5.14701550e-03  7.86485701e-03
  -5.91738161e-04  3.52433389e-03  5.75197931e-03  6.32847867e-03
   1.39286365e-03]
 [ 2.53302282e-03  1.36162033e-03  7.35520441e-03  8.87777137e-03
   1.21788131e-03 -5.30078722e-04  2.59244046e-03 -5.10416383e-04
   8.84916264e-03  2.00619318e-03  8.22429215e-03  8.22534912e-03
   7.87019554e-03 -8.09749798e-04  5.28440372e-03  7.36527062e-03
   7.74169891e-03]
 [ 3.36416106e-03 -4.10251359e-05  6.38385200e-03  9.17354318e-03
   3.40438272e-03  5.06247020e-03  2.93108922e-03 -2.71652919e-04
   3.277

### Results

In [16]:
training_predictions_normal = predict(X_train, Y_train, weights_normal, activations_normal, "Train",TAKE_BIAS,error_function,weight_types_NN)
test_predictions_normal = predict(X_test, Y_test, weights_normal, activations_normal, "Test",TAKE_BIAS,error_function,weight_types_NN)
training_predictions_wavelet = predict(X_train, Y_train, weights_wavelet, activations_wavelet, "Train",TAKE_BIAS,error_function,weight_types_WNN)
test_predictions_wavelet = predict(X_test, Y_test, weights_wavelet, activations_wavelet, "Test",TAKE_BIAS,error_function,weight_types_WNN)

Normal Neural Network: Train Cost: 0.4994754124250561
Normal Neural Network: Train Accuracy: 0.16666666666666666
Normal Neural Network: Test Cost: 0.4994341360143463
Normal Neural Network: Test Accuracy: 0.16666666666666666
Wavelet Neural Network: Train Cost: nan
Wavelet Neural Network: Train Accuracy: 0.173015873015873
Wavelet Neural Network: Test Cost: nan
Wavelet Neural Network: Test Accuracy: 0.15185185185185185


Fin.